In [1]:
# mount filesystem and install requirements
from google.colab import drive
drive.mount('/content/gdrive')
%cd /content/gdrive/MyDrive/ONR
#!pip install dgl==0.4.3 rdflib dglke
#!pip install pandas==1.3.0
#!pip install tzwhere
import pandas as pd
# import dgl
# import dglke
import torch as th
import pickle
import numpy as np
import re

Mounted at /content/gdrive
/content/gdrive/MyDrive/ONR


In [2]:
wqsites = pd.read_csv('wqsites14.csv')
print(wqsites.head(2))
print(len(wqsites))
!wc -l /content/gdrive/MyDrive/ONR/wqsample14-full.tsv

/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:2718: DtypeWarning: Columns (8,10,21,27,28,29) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


  OrganizationIdentifier  ... ProviderName
0                USGS-AR  ...         NWIS
1                USGS-AR  ...         NWIS

[2 rows x 36 columns]
27654
33405912 /content/gdrive/MyDrive/ONR/wqsample14-full.tsv


In [3]:
#!curl -X POST --header 'Content-Type: application/json' --header 'Accept: application/zip' -d '{"sampleMedia":["Water","water"],"startDateLo":"06-01-2014","startDateHi":"12-31-2014","dataProfile":"resultPhysChem","providers":["NWIS","STEWARDS","STORET"]}' 'https://www.waterqualitydata.us/data/Result/search?mimeType=csv&zip=yes' -o wq14raw-physchem-2.zip
#!curl -X POST --header 'Content-Type: application/json' --header 'Accept: application/zip' -d '{"sampleMedia":["Water","water"],"startDateLo":"06-01-2014","startDateHi":"12-31-2014","dataProfile":"biological","providers":["NWIS","STEWARDS","STORET"]}' 'https://www.waterqualitydata.us/data/Result/search?mimeType=csv&zip=yes' -o wq14raw-bio-2.zip

In [4]:
#!mv wq14raw.zip wq14raw-physchem.zip
#!ls -al wq14raw*
#!mv biologicalresult.csv biologicalresult-tmp1.csv
#!unzip wq14raw-bio-2.zip
#!head biologicalresult.csv
#!wc -l biologicalresult.csv      #8050249
#!wc -l biologicalresult-tmp1.csv #4918984
#!cp biologicalresult-tmp1.csv biologicalresult-tmpxx.csv
#!cat biologicalresult.csv >> biologicalresult-tmpxx.csv
#!wc -l biologicalresult-tmpxx.csv
#!mv biologicalresult-tmpxx.csv biologicalresult.csv
#!rm biologicalresult-tmp1.csv
#!mv biologicalresult.csv biologicalresult-wateronly-allbodies-2014.csv

#--header 'Accept: application/zip'
# !curl -v --header 'Content-Type: application/json'  \
#   -d '{"siteType":["Ocean","Estuary","Lake, Reservoir, Impoundment","Stream"],"sampleMedia":["Water","water"],"startDateLo":"06-01-2014","startDateHi":"12-31-2014","dataProfile":"biological","providers":["NWIS","STEWARDS","STORET"]}'\
#   'https://www.waterqualitydata.us/data/Result/search?mimeType=csv&zip=yes' -o xx


# !curl -O -X POST --header 'Content-Type: application/json'  \
#   -d '{"siteType":["Ocean","Estuary","Lake, Reservoir, Impoundment","Stream"],"sampleMedia":["Water","water"],"startDateLo":"06-01-2014","startDateHi":"12-31-2014","dataProfile":"biological","providers":["NWIS","STEWARDS","STORET"]}'\
#   'https://www.waterqualitydata.us/data/Station/search?mimeType=csv&zip=no' -o wqsites14-bio-waterbodies-stations.csv

# !curl -X POST --header 'Content-Type: application/json' --header 'Accept: application/zip'\
#   -d '{"sampleMedia":["Water","water"],"startDateLo":"01-01-2014","startDateHi":"12-31-2014","dataProfile":"narrowResult","providers":["STEWARDS"]}'\
#   'https://www.waterqualitydata.us/data/Result/search?mimeType=csv&zip=no' -o wqsites14-narrowresult-stewards.csv

!ls -al *.csv *.zip

#!curl --header 'Content-Type: application/json' -d '{"siteType":["Ocean","Estuary","Lake, Reservoir, Impoundment","Stream"],"sampleMedia":["Water","water"],"startDateLo":"01-01-2014","startDateHi":"05-31-2014","dataProfile":"biological","providers":["NWIS","STEWARDS","STORET"]}' 'https://www.waterqualitydata.us/data/Result/search?mimeType=csv&zip=yes'

# !curl -O -X POST --header 'Content-Type: application/json' --header 'Accept: application/zip' \
#   -d '{"siteType":["","Ocean","Estuary","Lake, Reservoir, Impoundment","Stream"],"sampleMedia":["Water","water"],"startDateLo":"01-01-2014","startDateHi":"5-31-2014","dataProfile":"biological","providers":["NWIS","STEWARDS","STORET"]}'\
#   'https://www.waterqualitydata.us/data/Result/search?mimeType=csv&zip=yes'


#!curl -O -X POST --header 'Content-Type: application/json' --header 'Accept: application/zip' -d '{"providers":["NWIS","STEWARDS","STORET"]}' 'https://www.waterqualitydata.us/data/Station/search?mimeType=csv&zip=yes'

#!sed -i '1d' biologicalresult.csv
#!ls -al wq14raw* biological* phys*
#!head biological resultphyschem.csv

#wqphy = pd.read_csv('resultphyschem.csv')
#wqphy = None
#!sed '4852466q;d' biologicalresult.csv
# wqbio = pd.read_csv('resultphyschem.csv', #error_bad_lines=False,
#   usecols = ['ActivityStartDate', 'ActivityStartTime/Time', 'ActivityStartTime/TimeZoneCode',
#   'ActivityEndDate', 'ActivityEndTime/Time', 'ActivityEndTime/TimeZoneCode',
#   'ActivityDepthHeightMeasure/MeasureValue', 'ActivityDepthHeightMeasure/MeasureUnitCode',
#   'ActivityDepthHeightMeasure/MeasureValue', 'ActivityDepthHeightMeasure/MeasureUnitCode',
#   'MonitoringLocationIdentifier', 'CharacteristicName', 'ResultSampleFractionText',
#   'ResultMeasureValue', 'ResultMeasure/MeasureUnitCode', 'ProviderName']
# )

#xx

-rw------- 1 root root   25864975 Sep 12 11:36  apache-jena-4.2.0.zip
-rw------- 1 root root   62096310 Sep 12 11:36  apache-jena-fuseki-4.2.0.zip
-rw------- 1 root root  148794201 Jan 19 00:41 'Articles for Embeddings-20220118T225021Z-001.zip'
-rw------- 1 root root   10839037 Oct 31 16:51 'Beach Attributes - all beaches since 2014.csv'
-rw------- 1 root root   21575367 Jan 21 01:46  biologicalresult.csv
-rw------- 1 root root   52153829 Jan 21 01:37  biologicalresult-water-fecalcoliform.csv
-rw------- 1 root root 7736097276 Jan 20 17:54  biologicalresult-wateronly-allbodies-2014.csv
-rw------- 1 root root   18011144 Jan  9 21:49  kg-gnn-20220109T214849Z-001.zip
-rw------- 1 root root  290238657 Nov  4 14:34  national_single.zip
-rw------- 1 root root 3052289484 Jan 19 17:21  resultphyschem.csv
-rw------- 1 root root    1236496 Jan 21 00:29  stations-ocean-2014.csv
-rw------- 1 root root   14637900 Jan 21 00:25  stations-wateronly-2014.csv
-rw------- 1 root root    3084201 Dec  1 16:4

In [5]:
wqsites = pd.read_csv('stations-wateronly-2014.csv')
wqsites.head()

/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:2718: DtypeWarning: Columns (8,10,13,14,18,21,27) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


OrganizationIdentifier  ... ProviderName
0                    ARS  ...     STEWARDS
1                    ARS  ...     STEWARDS
2                    ARS  ...     STEWARDS
3                    ARS  ...     STEWARDS
4                    ARS  ...     STEWARDS

[5 rows x 36 columns]

In [ ]:
!#wqphy[wqphy['CharacteristicName'] == 'Specific conductance']['ResultMeasure/MeasureUnitCode'].value_counts()
#wqphy[wqphy['CharacteristicName'].str.contains('Baro')].value_counts(['CharacteristicName', 'ResultSampleFractionText', 'ResultMeasure/MeasureUnitCode']) \
#  .reset_index()[0:60]

In [ ]:
#wqbio[wqbio['CharacteristicName'] == 'Specific conductance']['ResultMeasure/MeasureUnitCode'].value_counts()

In [ ]:
#!curl -X POST --header 'Content-Type: application/json' --header 'Accept: application/zip' -d '{"sampleMedia":["Water","water"],"startDateLo":"01-01-2014","startDateHi":"05-31-2014","dataProfile":"biological","providers":["NWIS","STEWARDS","STORET"]}' 'https://www.waterqualitydata.us/data/Result/search?mimeType=csv&zip=yes' -o wq14raw-bio.zip

In [ ]:
!ls *.zip

In [ ]:
#!head -n 100 '/content/gdrive/MyDrive/ONR/wqdata14.csv' > '/content/gdrive/MyDrive/ONR/wqdata14-sm.csv'
#!tail -n 100 '/content/gdrive/MyDrive/ONR/wqdata14.csv' >> '/content/gdrive/MyDrive/ONR/wqdata14-sm.csv'
#!cat '/content/gdrive/MyDrive/ONR/wqdata14-sm.csv'

In [7]:
wqsites = pd.read_csv('wqsites14.csv')
wqsites.head(2)

/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:2718: DtypeWarning: Columns (8,10,21,27,28,29) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


OrganizationIdentifier  ... ProviderName
0                USGS-AR  ...         NWIS
1                USGS-AR  ...         NWIS

[2 rows x 36 columns]

In [18]:
# map of all storet/nwis sites
import plotly.express as px
import pandas as pd
import plotly.graph_objects as go
from geopy import distance

wqsites = pd.read_csv('stations-wateronly-2014.csv')
wqsites.head()

fig = px.scatter(x=wqsites['LatitudeMeasure'], y=wqsites['LongitudeMeasure'])
fig.update_layout(mapbox_style="open-street-map", mapbox_zoom=4, mapbox_center_lat = 41,
  mapbox_center_lon = -80,
  margin={"r":0,"t":0,"l":0,"b":0})#stamen-terrain
fig.add_scattermapbox(
  lat=wqsites['LatitudeMeasure'], lon=wqsites['LongitudeMeasure'],
  mode = 'markers+text',
  #text = swnam,
  marker_size=6,
  marker_color='rgb(235, 0, 100)'
)
fig.show()

/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:2718: DtypeWarning:

Columns (8,10,13,14,18,21,27) have mixed types.Specify dtype option on import or set low_memory=False.



In [19]:
# map of "ocean" storet/nwis sites
import plotly.express as px
import pandas as pd
import plotly.graph_objects as go
from geopy import distance

wqsites = pd.read_csv('stations-ocean-2014.csv')
#wqsites.head()

fig = px.scatter(x=wqsites['LatitudeMeasure'], y=wqsites['LongitudeMeasure'])
fig.update_layout(mapbox_style="open-street-map", mapbox_zoom=4, mapbox_center_lat = 41,
  mapbox_center_lon = -80,
  margin={"r":0,"t":0,"l":0,"b":0})#stamen-terrain
fig.add_scattermapbox(
  lat=wqsites['LatitudeMeasure'], lon=wqsites['LongitudeMeasure'],
  mode = 'markers+text',
  #text = swnam,
  marker_size=6,
  marker_color='rgb(235, 0, 100)'
)
fig.show()

In [17]:
# nwis/storet sites vs beacon beaches
import plotly.express as px
import pandas as pd
import plotly.graph_objects as go
from geopy import distance

wqsites = pd.read_csv('stations-wateronly-2014.csv')

df2 = pd.read_csv('/content/gdrive/MyDrive/ONR/Beach Attributes - all beaches since 2014.csv')
df2 = df2.dropna( # drops NAs (drops ~= 8000 or 10%)
  subset=['Start Latitude', 'Start Longitude', 'End Latitude', 'End Longitude'])
df2 = df2[~((df2['Start Latitude'] == df2['Start Longitude']) | (df2['Start Latitude'] == df2['End Longitude']) | (df2['End Latitude'] == df2['Start Longitude']) | (df2['End Latitude'] == df2['End Longitude']))] #216
df2 = df2.drop_duplicates(['Beach ID', 'Beach Name', 'Start Latitude', 'Start Longitude', 'End Latitude', 'End Longitude']) # from 79k to 9k
# df2 = df2[df2['State'] == st]
# dist col
# for index, row in df2.iterrows():
#   df2.loc[index, 'dist'] = distance.distance(
#     (row['Start Latitude'], row['Start Longitude']),
#     (row['End Latitude'], row['End Longitude'])
#   ).miles
# df2 = df2[~(df2['dist'] > 50)] # 16
dfs = pd.DataFrame({'lat': [], 'lon': [], 'idx': []})
c = 0
for index, row in df2.iterrows():
  x = pd.DataFrame({
    'lat': [row['Start Latitude'], row['End Latitude'], None], #None to break the polyline
    'lon': [row['Start Longitude'], row['End Longitude'], None],
    'idx': [c, c, None]})
  dfs = dfs.append(x)
  c += 1

# fig = go.Figure()
# fig.add_trace(
fig = px.line_mapbox(dfs, lat="lat", lon="lon", hover_name="idx", zoom=3, height=600) #, color="State"

fig.update_layout(mapbox_style="open-street-map", mapbox_zoom=4, mapbox_center_lat = 41,
  mapbox_center_lon = -80,
  margin={"r":0,"t":0,"l":0,"b":0})#stamen-terrain

fig.add_scattermapbox(
  lat=wqsites['LatitudeMeasure'], lon=wqsites['LongitudeMeasure'],
  mode = 'markers+text',
  #text = swnam,
  marker_size=6,
  marker_color='rgb(235, 0, 100)'
)

fig.show()

/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:2718: DtypeWarning:

Columns (8,10,13,14,18,21,27) have mixed types.Specify dtype option on import or set low_memory=False.



In [11]:
# So the nwis/beacon sites are more numerous than beacon.
# But are the samples at all relevant in comparison to beacon?
# E.g. limit the storet sites to only those
# with fecal indictor bacteria. Then are the sites similar in
# number to beacon, or still more (and more or less precise)?
# Starting with Fecal Coliform:
fc = pd.read_csv('biologicalresult-water-fecalcoliform.csv')
fc.head()

/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:2718: DtypeWarning:

Columns (13,16,17,18,25,26,36,68,71,83,84,88,95,135) have mixed types.Specify dtype option on import or set low_memory=False.



OrganizationIdentifier  ... ProviderName
0                  NJHDG  ...       STORET
1           21FLSARA_WQX  ...       STORET
2                   DRBC  ...       STORET
3             NJDEP_BMWM  ...       STORET
4           21FLSEAS_WQX  ...       STORET

[5 rows x 156 columns]

In [12]:
# na loc
print(len(fc[fc['ActivityLocation/LatitudeMeasure'].isna()])) #3500
print(len(fc)) #90k
fc = fc.dropna(subset=['ActivityLocation/LatitudeMeasure'])

3507
89821


In [13]:
# na result
print(len(fc[fc['DetectionQuantitationLimitMeasure/MeasureValue'].isna()])) # 56k / 86k (30k non-NA)
fc['DetectionQuantitationLimitMeasure/MeasureValue'] = fc['DetectionQuantitationLimitMeasure/MeasureValue'].fillna(0)

56258


In [14]:
# what are the # of samples at each location?
# MonitoringLocationIdentifier

# 81k
fc[['MonitoringLocationIdentifier', 'ActivityStartDate']].value_counts()
fc[['MonitoringLocationIdentifier', 'ActivityStartDate']].value_counts()[0:20]

MonitoringLocationIdentifier  ActivityStartDate
21FLWQA_WQX-GTMPCNUT          2014-07-09           7
                              2014-04-09           7
                              2014-12-03           7
                              2014-11-04           7
                              2014-10-20           7
                              2014-09-18           7
                              2014-08-07           7
                              2014-02-26           7
                              2014-03-11           7
                              2014-05-12           7
SKOKDATA_WQX-SWQM-2           2014-01-16           6
SKOKDATA_WQX-SWQM-13          2014-01-16           6
SKOKDATA_WQX-SS 117           2014-02-10           6
SKOKDATA_WQX-SS 103           2014-02-10           6
21FLWQA_WQX-GTMPCNUT          2014-02-25           6
                              2014-03-10           6
21FLGTM_WQX-GTMPCNUT          2014-01-12           6
21FLWQA_WQX-GTMPCNUT          2014-05-11           

In [16]:
# map: storet/nwis "fecal coliform" vs. beacon all

import plotly.express as px
import pandas as pd
import plotly.graph_objects as go
from geopy import distance

df2 = pd.read_csv('/content/gdrive/MyDrive/ONR/Beach Attributes - all beaches since 2014.csv')
df2 = df2.dropna( # drops NAs (drops ~= 8000 or 10%)
  subset=['Start Latitude', 'Start Longitude', 'End Latitude', 'End Longitude'])
df2 = df2[~((df2['Start Latitude'] == df2['Start Longitude']) | (df2['Start Latitude'] == df2['End Longitude']) | (df2['End Latitude'] == df2['Start Longitude']) | (df2['End Latitude'] == df2['End Longitude']))] #216
df2 = df2.drop_duplicates(['Beach ID', 'Beach Name', 'Start Latitude', 'Start Longitude', 'End Latitude', 'End Longitude']) # from 79k to 9k

dfs = pd.DataFrame({'lat': [], 'lon': [], 'idx': []})
c = 0
for index, row in df2.iterrows():
  x = pd.DataFrame({
    'lat': [row['Start Latitude'], row['End Latitude'], None], #None to break the polyline
    'lon': [row['Start Longitude'], row['End Longitude'], None],
    'idx': [c, c, None]})
  dfs = dfs.append(x)
  c += 1

# fig = go.Figure()
# fig.add_trace(
fig = px.line_mapbox(dfs, lat="lat", lon="lon", hover_name="idx", zoom=3, height=600) #, color="State"

fig.update_layout(mapbox_style="open-street-map", mapbox_zoom=4, mapbox_center_lat = 41,
  mapbox_center_lon = -80,
  margin={"r":0,"t":0,"l":0,"b":0})#stamen-terrain

fig.add_scattermapbox(
  lat=fc['ActivityLocation/LatitudeMeasure'], lon=fc['ActivityLocation/LongitudeMeasure'],
  mode = 'markers+text',
  #text = swnam,
  marker_size=6,
  marker_color='rgb(235, 0, 100)'
)

fig.show()

In [20]:
# beacon 2014
import pandas as pd
df = pd.read_sas('/content/gdrive/MyDrive/ONR/beacon2014.sas7bdat')
df['VAR3'] = df['VAR3'].str.decode('utf-8')
df.head(10)

State_Code    Year  ... WQvalue analysistime
0      b'CT'  2014.0  ...     NaN          NaN
1      b'CT'  2014.0  ...     NaN          NaN
2      b'CT'  2014.0  ...     NaN          NaN
3      b'CT'  2014.0  ...     NaN          NaN
4      b'CT'  2014.0  ...     NaN          NaN
5      b'CT'  2014.0  ...     NaN          NaN
6      b'CT'  2014.0  ...     NaN          NaN
7      b'CT'  2014.0  ...     5.0          NaN
8      b'CT'  2014.0  ...     NaN          NaN
9      b'CT'  2014.0  ...     NaN          NaN

[10 rows x 20 columns]

In [21]:
len(df[df['VAR13'] == b'Fecal Coliform']) # 15k
df = df[df['VAR13'] == b'Fecal Coliform']
# beach+date
df[['VAR3', 'VAR9']].value_counts() # 6631
#df[['VAR3', 'VAR9']].value_counts()[0:60]
# histogram these?

VAR3      VAR9      
CA845616  2014-12-08    33
          2014-11-24    32
          2014-11-13    32
          2014-03-31    30
          2014-03-17    30
                        ..
CA643858  2014-09-23     1
          2014-09-24     1
          2014-09-25     1
          2014-09-26     1
AK488647  2014-07-06     1
Length: 6631, dtype: int64

In [22]:
# merging beach+beach attrs
#df1.merge(df2, left_on='lkey', right_on='rkey')
df2 = pd.read_csv('/content/gdrive/MyDrive/ONR/Beach Attributes - all beaches since 2014.csv')
df2 = df2.dropna( # drops NAs (drops ~= 8000 or 10%)
  subset=['Start Latitude', 'Start Longitude', 'End Latitude', 'End Longitude'])
df2 = df2[~((df2['Start Latitude'] == df2['Start Longitude']) | (df2['Start Latitude'] == df2['End Longitude']) | (df2['End Latitude'] == df2['Start Longitude']) | (df2['End Latitude'] == df2['End Longitude']))] #216
df2 = df2.drop_duplicates(['Beach ID', 'Beach Name', 'Start Latitude', 'Start Longitude', 'End Latitude', 'End Longitude']) # from 79k to 9k
#df2.head()
#x = 
df = df.merge(df2, left_on='VAR3', right_on='Beach ID')

In [23]:
df.head()

State_Code  ...  AdvisoryReportingFrequencyUnits
0      b'LA'  ...                         PER_YEAR
1      b'LA'  ...                         PER_YEAR
2      b'LA'  ...                         PER_YEAR
3      b'LA'  ...                         PER_YEAR
4      b'LA'  ...                         PER_YEAR

[5 rows x 36 columns]

In [25]:
# total samples - beacon
x = df[['VAR3', 'VAR9']].value_counts().reset_index()\
  .groupby(by='VAR3').sum().reset_index().sort_values(by=0)
x.columns.values[1] = 'sum' #= x.columns.str.replace('0', 'sum')
x # 10k unique locations
df2 = df.groupby(by='VAR3').mean().reset_index()# (meaningless mean at least preserves lat/lon)
#fc2
cols = ['VAR3', 'Start Latitude', 'Start Longitude', 'End Latitude', 'End Longitude', 'sum']
x = x.merge(df2, left_on='VAR3', right_on='VAR3')[cols]
df2 = x
df2['size'] = round(df2['sum'] / 20) + 6
df2['lat'] = (df2['Start Latitude'] + df2['End Latitude']) / 2
df2['lon'] = (df2['Start Longitude'] + df2['End Longitude']) / 2
df2

VAR3  Start Latitude  Start Longitude  ...  size        lat         lon
0    CA183895       33.722000      -118.333100  ...   6.0  33.716700 -118.318400
1    AK488647       60.386460      -151.304160  ...   6.0  60.387235 -151.307495
2    AK551272       60.552108      -151.276030  ...   7.0  60.551251 -151.268967
3    AK802097       60.543320      -151.265320  ...   7.0  60.448997 -151.264250
4    LA725358       29.757785       -93.586548  ...   7.0  29.757143  -93.592513
..        ...             ...              ...  ...   ...        ...         ...
96   CA412549       33.730700      -118.081600  ...  32.0  33.721450 -118.067450
97   CA853136       33.556800      -117.819600  ...  33.0  33.520900 -117.776200
98   CA735620       34.025000      -118.517000  ...  45.0  34.010000 -118.500800
99   CA298722       33.513500      -117.757000  ...  49.0  33.508150 -117.752100
100  CA845616       33.620900      -117.936700  ...  88.0  33.610200 -117.907900

[101 rows x 9 columns]

In [31]:
# unique states in beacon for FC
pd.unique(df['State_Code'])

array([b'LA', b'CA', b'AK'], dtype=object)

In [26]:
# total samples - storet/nwis
x = fc[['MonitoringLocationIdentifier', 'ActivityStartDate']].value_counts().reset_index()\
  .groupby(by='MonitoringLocationIdentifier').sum().reset_index().sort_values(by=0)
x.columns.values[1] = 'sum' #= x.columns.str.replace('0', 'sum')
x # 10k unique locations
fc2 = fc.groupby(by='MonitoringLocationIdentifier').mean().reset_index()# (meaningless mean at least preserves lat/lon)
#fc2
cols = ['MonitoringLocationIdentifier', 'ActivityLocation/LatitudeMeasure', 'ActivityLocation/LongitudeMeasure', 'sum']
x = x.merge(fc2, left_on='MonitoringLocationIdentifier', right_on='MonitoringLocationIdentifier')[cols]
fc2 = x
fc2['size'] = round(fc2['sum'] / 20) + 6
fc2
# fc = fc.merge(x, left_on='MonitoringLocationIdentifier', right_on='MonitoringLocationIdentifier')
# fc
#fc.merge(x, how='right', left_on='MonitoringLocationIdentifier', right_on='MonitoringLocationIdentifier')['sum']

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:10: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



MonitoringLocationIdentifier  ActivityLocation/LatitudeMeasure  ...  sum  size
0             WVDEP_WIB_WQX-CCPT04                         39.503964  ...    1   6.0
1                21NC03WQ-B9740000                         34.251830  ...    1   6.0
2                21NC03WQ-C3900000                         35.298180  ...    1   6.0
3                21NC03WQ-C4360000                         35.658320  ...    1   6.0
4                21NC03WQ-C7000000                         35.166660  ...    1   6.0
...                            ...                               ...  ...  ...   ...
10381                21CABCH-HYPS7                         33.996620  ...  258  19.0
10382                21CABCH-HYPS6                         34.004970  ...  258  19.0
10383                21CABCH-HYPS5                         34.008060  ...  258  19.0
10384               21CABCH-HYPCB1                         33.713330  ...  258  19.0
10385               21CABCH-HYPCB2                         33.711380  ...  258  19.0

[10386 rows x 5 columns]

In [30]:
# "fecal coliform" data in nwis/storet vs. beacon

import plotly.express as px
import pandas as pd
import plotly.graph_objects as go
from geopy import distance

# df2 = pd.read_csv('/content/gdrive/MyDrive/ONR/Beach Attributes - all beaches since 2014.csv')
# df2 = df2.dropna( # drops NAs (drops ~= 8000 or 10%)
#   subset=['Start Latitude', 'Start Longitude', 'End Latitude', 'End Longitude'])
# df2 = df2[~((df2['Start Latitude'] == df2['Start Longitude']) | (df2['Start Latitude'] == df2['End Longitude']) | (df2['End Latitude'] == df2['Start Longitude']) | (df2['End Latitude'] == df2['End Longitude']))] #216
# df2 = df2.drop_duplicates(['Beach ID', 'Beach Name', 'Start Latitude', 'Start Longitude', 'End Latitude', 'End Longitude']) # from 79k to 9k

dfs = pd.DataFrame({'lat': [], 'lon': [], 'idx': []})
c = 0
for index, row in df2.iterrows():
  x = pd.DataFrame({
    'lat': [row['Start Latitude'], row['End Latitude'], None], #None to break the polyline
    'lon': [row['Start Longitude'], row['End Longitude'], None],
    'idx': [c, c, None]})
  dfs = dfs.append(x)
  c += 1

# fig = go.Figure()
# fig.add_trace(
fig = px.line_mapbox(dfs, lat="lat", lon="lon", hover_name="idx", zoom=3, height=600) #, color="State"

fig.update_layout(mapbox_style="open-street-map", mapbox_zoom=4, mapbox_center_lat = 41,
  mapbox_center_lon = -80,
  margin={"r":0,"t":0,"l":0,"b":0})#stamen-terrain

fig.add_scattermapbox(
  lat=fc2['ActivityLocation/LatitudeMeasure'], lon=fc2['ActivityLocation/LongitudeMeasure'],
  mode = 'markers+text',
  #text = swnam,
  text = '#samples: ' + fc2['sum'].astype(str) + ' (nwis/storet)',
  marker_size=fc2['size'],#6,
  marker_color='rgb(0, 90, 181)'
)

fig.add_scattermapbox(
  lat=df2['lat'], lon=df2['lon'],
  mode = 'markers+text',
  text = '#samples: ' + df2['sum'].astype(str) + ' (beacon)',
  marker_size=df2['size'],#6,
  marker_color='rgb(220, 50, 32)'
)

fig.show()

# Building wqcc (10-binned continuous-only wq dataset with time and location info)

In [ ]:
with open('/content/gdrive/MyDrive/ONR/wq14+times.pkl', 'rb') as f:
  wq = pickle.load(f)
wq.head(4)

KeyboardInterrupt: ignored

Exception ignored in: 'pandas._libs.tslibs.conversion._localize_tso'
Traceback (most recent call last):
  File "pandas/_libs/tslibs/timezones.pyx", line 238, in pandas._libs.tslibs.timezones.get_dst_info
  File "pandas/_libs/tslibs/timezones.pyx", line 170, in pandas._libs.tslibs.timezones.get_utcoffset
  File "/usr/local/lib/python3.7/dist-packages/pytz/__init__.py", line 381, in utcoffset
    def utcoffset(self, dt):
KeyboardInterrupt: 


KeyboardInterrupt: ignored

In [ ]:
wq.head(20)
wq[wq['CharacteristicName'] == 'Specific conductance'].head(20)
wq[wq['CharacteristicName'] == 'Specific conductance']['ResultMeasure/MeasureUnitCode'].value_counts()
print(len(wq)) #3.1 mil, later reduced to 2.8 mil
#wq['ResultSampleFractionText'].fillna('None').value_counts()

In [ ]:
# 144 unique
wq['ResultMeasure/MeasureUnitCode'].value_counts()[0:60] 
# 1752 unique
wq['CharacteristicName'].value_counts().reset_index()[0:60]

In [ ]:
# 4437 unique
#pd.uniquewq['CharacteristicName'], wq['ResultMeasure/MeasureUnitCode'])
x = wq.copy()
x['ResultSampleFractionText'] = x['ResultSampleFractionText'].fillna('---')
x['ResultMeasure/MeasureUnitCode'] = x['ResultMeasure/MeasureUnitCode'].fillna('---')

x.value_counts(['CharacteristicName', 'ResultSampleFractionText', 'ResultMeasure/MeasureUnitCode']) \
  .reset_index()[0:60]

In [ ]:
wq[wq['CharacteristicName'].str.contains('Baro')].value_counts(['CharacteristicName', 'ResultSampleFractionText', 'ResultMeasure/MeasureUnitCode']) \
  .reset_index()[0:60]

In [ ]:
##
# Load wq+times (pre-generated times) instead
donotload
##
wq = pd.read_csv('/content/gdrive/MyDrive/ONR/wqdata14.csv')
wq.head()

In [ ]:
# wqsmaller
wq = wq[['ActivityStartDate', 'ActivityStartTime/Time', 'ActivityStartTime/TimeZoneCode',
  'ActivityEndDate', 'ActivityEndTime/Time', 'ActivityEndTime/TimeZoneCode',
  'ActivityDepthHeightMeasure/MeasureValue', 'ActivityDepthHeightMeasure/MeasureUnitCode',
  'ActivityDepthHeightMeasure/MeasureValue', 'ActivityDepthHeightMeasure/MeasureUnitCode',
  'MonitoringLocationIdentifier', 'CharacteristicName', 'ResultSampleFractionText',
  'ResultMeasureValue', 'ResultMeasure/MeasureUnitCode', 'ProviderName']]
wq.to_pickle("/content/gdrive/MyDrive/ONR/wq14-min.pkl")


In [ ]:
with open('/content/gdrive/MyDrive/ONR/wq14-min.pkl', 'rb') as f:
  wq = pickle.load(f)
wq.head()

In [ ]:
len(wq) #3.3m
# wq[wq['ActivityStartDate'].isna()]#0
# wq[wq['ActivityStartTime/Time'].isna()]#558k
len(wq[wq['starttime-utc'].isna()])#527
len(wq[wq['timestamp-start'].isna()]) #0
len(wq[wq['starttime'].isna()]) #527
#timestamp-start

In [ ]:
len(wqsites)

NameError: ignored

In [ ]:
# problem: 500k / 3mil do not have timezone - could be HA or EST!
# solution: every station has a lat/lon. using stations which do have an timezone,
#  find the nearest station for each NA timezone.
wqsites[wqsites['LatitudeMeasure'].isna()]  
wqsites[wqsites['LongitudeMeasure'].isna()] #0

In [ ]:
# solution: make a dict which has a timezone for every lat/lon integer pair
#wq[wq['ActivityStartTime/TimeZoneCode'].isna()] #558k
#wq[wq['MonitoringLocationIdentifier'].isna()] #0
#wq[wq['ActivityStartTime/TimeZoneCode'].isna()]['MonitoringLocationIdentifier'].value_counts() # >4k unique station ids
#list(
#  wq[wq['ActivityStartTime/TimeZoneCode'].isna()]['MonitoringLocationIdentifier'].value_counts().rename_axis('unique_values').reset_index(name='counts')['unique_values']
#)
wqsites['latint'] = (wqsites['LatitudeMeasure'].astype(float) / 10).round(0)
wqsites['lonint'] = (wqsites['LongitudeMeasure'].astype(float) / 10).round(0)
#wq['lat'] = wqsites[wqsites['MonitoringLocationIdentifier'] == wq['MonitoringLocationIdentifier']]['LatitudeMeasure']#.astype(int)
#joined = wq.join(wqsites, on='MonitoringLocationIdentifier')
wqsites_min = wqsites[['MonitoringLocationIdentifier', 'latint', 'lonint']]
wqj = pd.merge(wq, wqsites_min, on='MonitoringLocationIdentifier')
wqj.head(2)

In [ ]:
# Updates very slowly e.g. 1 second for one.
# c = 0
# for i, j in joined[joined['ActivityStartTime/TimeZoneCode'].isna()].iterrows():
#   #print(i, j)
#   joined.loc[joined.index == i, 'ActivityStartTime/TimeZoneCode'] = joined[
#     (joined['latint'] == j['latint']) &
#     (joined['lonint'] == j['lonint']) &
#     (joined['ActivityStartTime/TimeZoneCode'].isna() == False)
#   ].iloc[0]['ActivityStartTime/TimeZoneCode']
#   if c % 10000 == 0:
#     print('updated {}'.format(c))
#   c += 1

  #break
# ['ActivityStartTime/TimeZoneCode'] = \
#   pd.concat(
#     [ y['timestamp-start'].dt.tz_localize(whois_timezone_info[x]) for x,y in wq.groupby('ActivityStartTime/TimeZoneCode') ]
#   )
  #joined[(joined['ActivityStartTime/TimeZoneCode'].isna() == False) & (joined['latint'] ==)]

# chooses the highest 
# works for all but 6k
print(len(wqj[wqj['ActivityStartTime/TimeZoneCode'].isna()])) #558418
c = 0
for x, y in wqj.groupby(['latint', 'lonint']):
  if len(y[y['ActivityStartTime/TimeZoneCode'].isna()]) == 0: # no NAs
    continue
  if len(y[y['ActivityStartTime/TimeZoneCode'].isna() == False]) == 0: # all NAs
    continue

  print('x:',x,'len(y):',len(y))
  #print('isna():',y[y['ActivityStartTime/TimeZoneCode'].isna()])
  #print(y['ActivityStartTime/TimeZoneCode'].value_counts().rename_axis('unique_values').reset_index(name='counts')['unique_values'].iloc[0])
  
  wqj.loc[
    (wqj['latint'] == x[0]) & (wqj['lonint'] == x[1]) & (wqj['ActivityStartTime/TimeZoneCode'].isna()), 'ActivityStartTime/TimeZoneCode'
  ] = y['ActivityStartTime/TimeZoneCode'].value_counts().rename_axis('unique_values').reset_index(name='counts')['unique_values'].iloc[0]
  
  # wqj[
  #   (joined['latint'] == j['latint']) &
  #   (joined['lonint'] == j['lonint']) &
  #   (joined['ActivityStartTime/TimeZoneCode'].isna() == False)
  # ].iloc[0]['ActivityStartTime/TimeZoneCode']
  # c += 1
  # if c>10:
  #   break
print(len(wqj[wqj['ActivityStartTime/TimeZoneCode'].isna()]))

#wqj.loc[wqj['ActivityStartTime/TimeZoneCode'].isna(), 'ActivityStartTime/TimeZoneCode'] = 

# solution2: use tzwhere --- unreliable (#issues) and no loc code returned

# print(len(wqj[wqj['ActivityStartTime/TimeZoneCode'].isna()]))
# from tzwhere import tzwhere
# tz = tzwhere.tzwhere(forceTZ=True)
# #tz.tzNameAt(53.68193999999999, -6.239169999999998, forceTZ=True) #Europe/Dublin

# c = 0
# for x, y in wqj.groupby(['latint', 'lonint']):
#   print('x:',x,'len(y):',len(y))
#   print(x[0])
#   #print('isna():',y[y['ActivityStartTime/TimeZoneCode'].isna()])
#   #print('lenisna():',len(y[y['ActivityStartTime/TimeZoneCode'].isna()]))
#   #wqj.loc[y['ActivityStartTime/TimeZoneCode'].isna(), 'ActivityStartTime/TimeZoneCode'] = 
#   c += 1
#   if c>10:
#     break
# print(len(wqj[wqj['ActivityStartTime/TimeZoneCode'].isna()]))


In [ ]:
# Generating add'l time data

### 
# Do not run additional time. Instead, just load the pickle file associated
# with result of this cell.
dontrun
###

# MonitoringLocationIdentifier (ex "USGS-481648092242301")
#   CharacteristicName 	  ResultSampleFractionText 	ResultMeasureValue 	ResultMeasure/MeasureUnitCode
#ex Barometric pressure 	NaN 	                    750 	              mm/Hg
#wq = pd.read_csv('/content/gdrive/MyDrive/ONR/wqdata14.csv')

#Na
#print(len(wq[wq['ResultMeasureValue'].isna()]) / len(wq)) #240147 (7.2%)
#len(wq) #3354963
wq = wqj.dropna(subset=['ResultMeasureValue'])
wq = wq.dropna(subset=['ActivityStartTime/TimeZoneCode'])

#len(wq) #3114816
#len(wq[wq['ActivityStartDate'].isna() == False])              # 3114816
#len(wq[wq['ActivityStartTime/Time'].isna() == False])         # 2587170 (83.1% w/starttime)
#len(wq[wq['ActivityStartTime/TimeZoneCode'].isna() == False]) # 2587170

# tz (via gh)
whois_timezone_info = {  "A": 1 * 3600,  "ACDT": 10   * 3600,  "ACST": 9   * 3600,  "ACT": -5 * 3600,  "ACWST": 8   * 3600,  "ADT": 4 * 3600,  "AEDT": 11 * 3600,  "AEST": 10 * 3600,  "AET": 10 * 3600,  "AFT": 4   * 3600,  "AKDT": -8 * 3600,  "AKST": -9 * 3600,  "ALMT": 6 * 3600,  "AMST": -3 * 3600,  "AMT": -4 * 3600,  "ANAST": 12 * 3600,  "ANAT": 12 * 3600,  "AQTT": 5 * 3600,  "ART": -3 * 3600,  "AST": 3 * 3600,  "AT": -4 * 3600,  "AWDT": 9 * 3600,  "AWST": 8 * 3600,  "AZOST": 0 * 3600,  "AZOT": -1 * 3600,  "AZST": 5 * 3600,  "AZT": 4 * 3600,  "AoE": -12 * 3600,  "B": 2 * 3600,  "BNT": 8 * 3600,  "BOT": -4 * 3600,  "BRST": -2 * 3600,  "BRT": -3 * 3600,  "BST": 6 * 3600,  "BTT": 6 * 3600,  "C": 3 * 3600,  "CAST": 8 * 3600,  "CAT": 2 * 3600,  "CCT": 6   * 3600,  "CDT": -5 * 3600,  "CEST": 2 * 3600,  "CET": 1 * 3600,  "CHADT": 13   * 3600,  "CHAST": 12   * 3600,  "CHOST": 9 * 3600,  "CHOT": 8 * 3600,  "CHUT": 10 * 3600,  "CIDST": -4 * 3600,  "CIST": -5 * 3600,  "CKT": -10 * 3600,  "CLST": -3 * 3600,  "CLT": -4 * 3600,  "COT": -5 * 3600,  "CST": -6 * 3600,  "CT": -6 * 3600,  "CVT": -1 * 3600,  "CXT": 7 * 3600,  "ChST": 10 * 3600,  "D": 4 * 3600,  "DAVT": 7 * 3600,  "DDUT": 10 * 3600,  "E": 5 * 3600,  "EASST": -5 * 3600,  "EAST": -6 * 3600,  "EAT": 3 * 3600,  "ECT": -5 * 3600,  "EDT": -4 * 3600,  "EEST": 3 * 3600,  "EET": 2 * 3600,  "EGST": 0 * 3600,  "EGT": -1 * 3600,  "EST": -5 * 3600,  "ET": -5 * 3600,  "F": 6 * 3600,  "FET": 3 * 3600,  "FJST": 13 * 3600,  "FJT": 12 * 3600,  "FKST": -3 * 3600,  "FKT": -4 * 3600,  "FNT": -2 * 3600,  "G": 7 * 3600,  "GALT": -6 * 3600,  "GAMT": -9 * 3600,  "GET": 4 * 3600,  "GFT": -3 * 3600,  "GILT": 12 * 3600,  "GMT": 0 * 3600,  "GST": 4 * 3600,  "GYT": -4 * 3600,  "H": 8 * 3600,  "HDT": -9 * 3600,  "HKT": 8 * 3600,  "HOVST": 8 * 3600,  "HOVT": 7 * 3600,  "HST": -10 * 3600,  "I": 9 * 3600,  "ICT": 7 * 3600,  "IDT": 3 * 3600,  "IOT": 6 * 3600,  "IRDT": 4   * 3600,  "IRKST": 9 * 3600,  "IRKT": 8 * 3600,  "IRST": 3   * 3600,  "IST": 5   * 3600,  "JST": 9 * 3600,  "K": 10 * 3600,  "KGT": 6 * 3600,  "KOST": 11 * 3600,  "KRAST": 8 * 3600,  "KRAT": 7 * 3600,  "KST": 9 * 3600,  "KUYT": 4 * 3600,  "L": 11 * 3600,  "LHDT": 11 * 3600,  "LHST": 10   * 3600,  "LINT": 14 * 3600,  "M": 12 * 3600,  "MAGST": 12 * 3600,  "MAGT": 11 * 3600,  "MART": 9   * 3600,  "MAWT": 5 * 3600,  "MDT": -6 * 3600,  "MHT": 12 * 3600,  "MMT": 6   * 3600,  "MSD": 4 * 3600,  "MSK": 3 * 3600,  "MST": -7 * 3600,  "MT": -7 * 3600,  "MUT": 4 * 3600,  "MVT": 5 * 3600,  "MYT": 8 * 3600,  "N": -1 * 3600,  "NCT": 11 * 3600,  "NDT": 2   * 3600,  "NFT": 11 * 3600,  "NOVST": 7 * 3600,  "NOVT": 7 * 3600,  "NPT": 5   * 3600,  "NRT": 12 * 3600,  "NST": 3   * 3600,  "NUT": -11 * 3600,  "NZDT": 13 * 3600,  "NZST": 12 * 3600,  "O": -2 * 3600,  "OMSST": 7 * 3600,  "OMST": 6 * 3600,  "ORAT": 5 * 3600,  "P": -3 * 3600,  "PDT": -7 * 3600,  "PET": -5 * 3600,  "PETST": 12 * 3600,  "PETT": 12 * 3600,  "PGT": 10 * 3600,  "PHOT": 13 * 3600,  "PHT": 8 * 3600,  "PKT": 5 * 3600,  "PMDT": -2 * 3600,  "PMST": -3 * 3600,  "PONT": 11 * 3600,  "PST": -8 * 3600,  "PT": -8 * 3600,  "PWT": 9 * 3600,  "PYST": -3 * 3600,  "PYT": -4 * 3600,  "Q": -4 * 3600,  "QYZT": 6 * 3600,  "R": -5 * 3600,  "RET": 4 * 3600,  "ROTT": -3 * 3600,  "S": -6 * 3600,  "SAKT": 11 * 3600,  "SAMT": 4 * 3600,  "SAST": 2 * 3600,  "SBT": 11 * 3600,  "SCT": 4 * 3600,  "SGT": 8 * 3600,  "SRET": 11 * 3600,  "SRT": -3 * 3600,  "SST": -11 * 3600,  "SYOT": 3 * 3600,  "T": -7 * 3600,  "TAHT": -10 * 3600,  "TFT": 5 * 3600,  "TJT": 5 * 3600,  "TKT": 13 * 3600,  "TLT": 9 * 3600,  "TMT": 5 * 3600,  "TOST": 14 * 3600,  "TOT": 13 * 3600,  "TRT": 3 * 3600,  "TVT": 12 * 3600,  "U": -8 * 3600,  "ULAST": 9 * 3600,  "ULAT": 8 * 3600,  "UTC": 0 * 3600,  "UYST": -2 * 3600,  "UYT": -3 * 3600,  "UZT": 5 * 3600,  "V": -9 * 3600,  "VET": -4 * 3600,  "VLAST": 11 * 3600,  "VLAT": 10 * 3600,  "VOST": 6 * 3600,  "VUT": 11 * 3600,  "W": -10 * 3600,  "WAKT": 12 * 3600,  "WARST": -3 * 3600,  "WAST": 2 * 3600,  "WAT": 1 * 3600,  "WEST": 1 * 3600,  "WET": 0 * 3600,  "WFT": 12 * 3600,  "WGST": -2 * 3600,  "WGT": -3 * 3600,  "WIB": 7 * 3600,  "WIT": 9 * 3600,  "WITA": 8 * 3600,  "WST": 14 * 3600,  "WT": 0 * 3600,  "X": -11 * 3600,  "Y": -12 * 3600,  "YAKST": 10 * 3600,  "YAKT": 9 * 3600,  "YAPT": 10 * 3600,  "YEKST": 6 * 3600,  "YEKT": 5 * 3600,  "Z": 0 * 3600,}
whois_timezone_info['HAST'] = -10 * 3600

# 558k entries have no start time, only date
wq['ActivityStartTime/Time'] = wq['ActivityStartTime/Time'].fillna('00:00:00')

# start time
wq['timestamp-start'] = pd.to_datetime(wq['ActivityStartDate'] + 'T' + wq['ActivityStartTime/Time'])
wq['starttime'] = pd.concat(
  [ y['timestamp-start'].dt.tz_localize(whois_timezone_info[x]) for x,y in wq.groupby('ActivityStartTime/TimeZoneCode') ]
)
wq['starttime-utc'] = pd.to_datetime(wq['starttime'], utc=True)
wq['starttime-delta'] = (wq['starttime-utc'] - pd.to_datetime('2014-01-01T00:00:00', utc=True)) \
  .astype('timedelta64[h]')
wq['starttime-delta'] = wq['starttime-delta'].fillna('0')
wq['starttime-delta'] = wq['starttime-delta'].astype(int)

# end time (not used)
# wq['timestamp-end'] = pd.to_datetime(wq['ActivityEndDate'] + 'T' + wq['ActivityEndTime/Time'])
# wq['endtime'] = pd.concat(
#   [ y['timestamp-end'].dt.tz_localize(whois_timezone_info[x]) for x,y in wq.groupby('ActivityEndTime/TimeZoneCode') ]
# )
# timespan (not used)
# wq['timespan'] = wq['endtime'] - wq['starttime']

wq['month-utc'] = wq['starttime-utc'].dt.month.astype('Int64')
wq['day-utc'] = wq['starttime-utc'].dt.day.astype('Int64')
wq['year-utc'] = wq['starttime-utc'].dt.year.astype('Int64')
wq['week-utc'] = wq['starttime-utc'].dt.week.astype('Int64')

# pickle
# wq['month-utc'] = wq['startime-utc'].dt.month.astype('Int64')
# wq['day-utc'] = wq['startime-utc'].dt.day.astype('Int64')
# wq['year-utc'] = wq['startime-utc'].dt.year.astype('Int64')
# wq['week-utc'] = wq['startime-utc'].dt.week.astype('Int64')
#wq['starttime-utc'] = wq['startime-utc']
wq = wq[['ActivityDepthHeightMeasure/MeasureValue', 'ActivityDepthHeightMeasure/MeasureUnitCode',
  'MonitoringLocationIdentifier', 'CharacteristicName', 'ResultSampleFractionText',
  'ResultMeasureValue', 'ResultMeasure/MeasureUnitCode', 'ProviderName',
  'timestamp-start', 'starttime', 'starttime-utc', 'starttime-delta', 'month-utc',
  'day-utc', 'year-utc', 'week-utc']] # not 'timestamp-end', 'endtime', 'timespan', 
wq.to_pickle("/content/gdrive/MyDrive/ONR/wq14+times.pkl")

#wqdata14-times
#wq[(wq['CharacteristicName'] == 'Enterococcus') & (wq['ResultMeasureValue'].isna())]
#wq['startime-utc'].dt.week

In [ ]:
wq['ActivityStartTime/TimeZoneCode'].value_counts()

In [ ]:
wq[(wq['timespan'].astype('timedelta64[h]') < 3) & (wq['timespan'].astype('timedelta64[h]') >= 0)]\
  ['timespan'].astype('timedelta64[m]').plot.hist(bins=60)

In [ ]:
wq[(wq['timespan'].astype('timedelta64[h]') < 3) & (wq['timespan'].astype('timedelta64[s]') > 0)]\
  ['timespan'].astype('timedelta64[m]').plot.hist(bins=60)

In [ ]:
wq[wq['timespan'].astype('timedelta64[h]') > 3]\
  ['timespan'].astype('timedelta64[D]').plot.hist(bins=60)

In [ ]:
wq[wq['timespan'].astype('timedelta64[h]') > 24]\
  ['timespan'].astype('timedelta64[D]').plot.hist(bins=60)

In [ ]:
# more than one sample at same station within a one-hour period?
# ...
# ...

In [ ]:
# locations
wq.MonitoringLocationIdentifier.value_counts().head(4) #USGS-481648092242301

In [ ]:
# wq continuous data (not categorical) + cleaned
wqcc = wq.copy()
wqcc = wqcc[
  ~wqcc['CharacteristicName'].str.contains(
    r'choice list|\(text\)|Odor, atmospheric|Oil and Grease|Tide stage|Fungi|Cloud cover', regex=True, case=False) &
  ~wqcc['ResultMeasureValue'].str.contains(
    r'[<>]|E[\-\+]|\*Not Reported', regex=True, case=False)]
print(len(wqcc), 'init') #2.981m

# drops non-numeric results (~1800)
# x = wqcc.copy()
# x['ResultMeasureValue'] = x['ResultMeasureValue'].fillna('')
# x = x[x['ResultMeasureValue'].str.contains(r'[^\d\.\-]', regex=True)]
wqcc = wqcc[~wqcc['ResultMeasureValue'].str.contains(r'[^\d\.\-]', regex=True)]

# drops value range, date, etc.
wqcc = wqcc[~wqcc['ResultMeasureValue'].str.contains(r'\d+-\d+', regex=True)]

# drops invalid decimals
wqcc = wqcc[~wqcc['ResultMeasureValue'].str.contains(r'\.\d+\.', regex=True)]


# ^[^\d]+$: drop e.g. ".", i.e. anything that does not contain at least one digit
wqcc['ResultMeasureValue'] = wqcc['ResultMeasureValue'].astype(str).str\
  .replace(r'\.\.', '.', regex=True)\
  .replace(r',', '', regex=True)\
  .replace(r'=', '', regex=True)\
  .replace(r'^[^\d]+$', np.nan, regex=True)
wqcc = wqcc.dropna(subset=['ResultMeasureValue'])

print(len(wqcc), 'end') #2.896

regex_pat = re.compile(r'none|nd|\*non-detect|\*non-detected|nt|uj', flags=re.IGNORECASE)
wqcc['ResultMeasureValue'] = wqcc['ResultMeasureValue'].astype(str).str.replace(regex_pat, '0', regex=True)

# fill na with blank
wqcc['ResultSampleFractionText'] = wqcc['ResultSampleFractionText'].fillna('')
wqcc['ResultMeasure/MeasureUnitCode'] = wqcc['ResultMeasure/MeasureUnitCode'].fillna('')

# wqcatg = pd.DataFrame(wqcc \
#   [['CharacteristicName', 'ResultSampleFractionText', 'ResultMeasure/MeasureUnitCode']] \
#   .copy().value_counts(['CharacteristicName', 'ResultSampleFractionText', 'ResultMeasure/MeasureUnitCode']))
# with pd.option_context('display.max_rows', None,
#   'display.max_columns', None,
#   'display.precision', 3,
#   ):
#   #print(wqcatg[wqcatg[0] > 10].sort_values(['CharacteristicName', 'ResultSampleFractionText', 'ResultMeasure/MeasureUnitCode'], ascending=True))
#   print(wqcatg.sort_values(['CharacteristicName', 'ResultSampleFractionText', 'ResultMeasure/MeasureUnitCode'], ascending=True))
#   # long-tail...

In [ ]:
# !pip show pandas
# !pip install pandas==1.3.0
# value_counts dropna not until 1.3.0
# empty strings not counted
# print(len(wq[(wq['CharacteristicName'] == 'Enterococcus')])) #95083
# print(len(wqcc[(wqcc['CharacteristicName'] == 'Enterococcus')])) # 88835
# print(len(wqcc[(wqcc['CharacteristicName'] == 'Enterococcus') & (wqcc['ResultSampleFractionText'] == '')]))
# print(len(wqcc[(wqcc['CharacteristicName'] == 'Enterococcus') & (wqcc['ResultSampleFractionText'].isna())])) # 81424
# print(len(wqcatg[[wqcatg['CharacteristicName'] == 'Enterococcus']]))

x = wqcc.copy()
x['ResultSampleFractionText'] = x['ResultSampleFractionText'].fillna('')
x['ResultMeasure/MeasureUnitCode'] = x['ResultMeasure/MeasureUnitCode'].fillna('')
x = x.value_counts(['CharacteristicName', 'ResultSampleFractionText', 'ResultMeasure/MeasureUnitCode']) \
  .reset_index()
  #.reset_index(name=['c','ce','cd'])
  #\# .rename_axis('unique_values') \
  
print(x)
print(x[x['CharacteristicName'] == 'Enterococcus'])

print(len(x[x[0] > 200]))
print(len(x[x[0] < 200]))
print(len(x[x[0] < 100]))

x.columns = ['CharacteristicName', 'ResultSampleFractionText', 'ResultMeasure/MeasureUnitCode', 'count']
wqcatg = x.copy()

#wqcatg.to_pickle("/content/gdrive/MyDrive/ONR/wqcatg14.pkl")

In [ ]:
# downsample continuous data to 10 bins
# todo: buckets should be for categorizing, but should not exclude points outside
#   of the distrib. but instead should simply merge those outliers into 0/10,
#   respectively
# requires at least 200 samples collected per category, where catg is unique
#   charname/fractext/unit
# todo: bins 3/5/10/20 and measure model performance
# not doing: remove anything that falls greatly outside of the normal distribution.
#   anything in the 99.9% of the curve, multiplied by 1.25, e.g. if 24C water temp
#   is 99.9%, then remove anything > 24*1.25
import matplotlib.pyplot as plt

from scipy.stats import norm
from sklearn.ensemble import RandomForestClassifier
from sklearn.preprocessing import LabelEncoder

label_encoder = LabelEncoder()
n_bins = 10

# n = pd.DataFrame(wqcatg[wqcatg['count'] > 100])
n = wqcatg[wqcatg['count'] > 200].copy()
#print(n)
c = 0
ndf = pd.DataFrame({
  'name': [],
  'frtx': [],
  'unit': [],
  'values': [],
  'times': [],
  'time-month': [],
  'time-week': [],
  'time-day': [],
  'locs': []}) # new df

for idx, i in n.iterrows():
  # print(idx)
  # print(idx, '--', i)
  # CharacteristicName               Temperature, water
  # ResultSampleFractionText                           
  # ResultMeasure/MeasureUnitCode                 deg C
  # count 
  name = i['CharacteristicName']
  rfct = i['ResultSampleFractionText']
  rmsr = i['ResultMeasure/MeasureUnitCode']
  count = i['count']
  #(name, rfct, rmsr, count) = idx
  v = wqcc[
    (wqcc['CharacteristicName'] == name) &
    (wqcc['ResultSampleFractionText'] == rfct) &
    (wqcc['ResultMeasure/MeasureUnitCode'] == rmsr)].copy()
  #v = v.fillna(0)
  print(name, rfct, rmsr, count)
  # print(v)
  # conversion...
  # if rmsr.lower() == 'ft':
  #   repl = lambda m: str(float(m.group(1)) / 12)
  #   v['ResultMeasureValue'] = v['ResultMeasureValue'].str.replace(r'^([\d\.\-]+)IN$', repl, regex=True)
  #   repl = lambda m: str(float(m.group(1)) * 3.28084)
  #   v['ResultMeasureValue'] = v['ResultMeasureValue'].str.replace(r'^([\d\.\-]+)M$', repl, regex=True)
  
  # choice list (todo)
  # if 'choice list' in name:
  #   y = pd.get_dummies(v['ResultMeasureValue'].astype(str))
  #   continue

  ##
  # This removes outlier values based on a normal distrib.
  ##
  # vx = v['ResultMeasureValue'].astype(float)
  # print(vx.min(),
  #   vx.max(),
  #   vx.quantile(0.001),
  #   vx.quantile(0.999))
  # q1 = vx.quantile(0.001) * 1.25
  # q2 = vx.quantile(0.999) * 1.25
  # v = v[~((vx < q1) | (vx > q2))]

  vx = v['ResultMeasureValue'].astype(float)
  y = label_encoder.fit_transform(pd.qcut(vx, n_bins, retbins=True, duplicates='drop')[0])
  
  ##
  # plots
  #vx.plot.hist(bins=10, figsize=(0.8,0.8))
  #plt.show()
  ##

  #ActivityStartDate
  #starttime
  #starttime-delta

  dfx = pd.DataFrame({
    'name': [name],
    'frtx': [rfct],
    'unit': [rmsr],
    'values': [y],
    'times': [v['starttime-delta'].to_list()],
    'time-month': [v['month-utc'].to_list()],
    'time-week': [v['week-utc'].to_list()],
    'time-day': [v['day-utc'].to_list()],
    'locs': [v['MonitoringLocationIdentifier'].to_list()],
    'simple-lat': [],
    'simple-lon': [],})
  ndf = ndf.append(dfx)

  #rfc = RandomForestClassifier(n_estimators=100, verbose=2)
  #x = rfc.fit(v[['ResultMeasureValue']].astype(float), y)
  #if c > 2:
  # break
  #c += 1

ndf.to_pickle("/content/gdrive/MyDrive/ONR/wq14.pkl")